In [1]:
import sys
from pathlib import Path
import qlib
import pandas as pd
from qlib.config import REG_CN
from qlib.contrib.model.gbdt import LGBModel
from qlib.contrib.data.handler import Alpha360
from qlib.utils import init_instance_by_config
from qlib.contrib.strategy import TopkDropoutStrategy
from qlib.contrib.report import analysis_model, analysis_position
# from qlib.contrib.evaluate import (
#     backtest as normal_backtest,
#     risk_analysis,
# )
from qlib.utils import exists_qlib_data, init_instance_by_config, flatten_dict
from qlib.workflow import R
from qlib.workflow.record_temp import SignalRecord, PortAnaRecord
from qlib.utils import flatten_dict
from qlib.data.dataset.loader import QlibDataLoader
from qlib.contrib.data.handler import Alpha158   #Alpha158内置指标体系
from qlib.data.dataset.loader import QlibDataLoader
import qlib
from qlib.contrib.data.handler import Alpha158   #Alpha158内置指标体系


provider_uri = "./qlib_data/cn_data"  # 原始行情数据存放目录
qlib.init(provider_uri=provider_uri, region=REG_CN)  # 初始化
market = "csi300"
benchmark = "SH000300"

#数据处理器参数配置
data_handler_config = {
    "start_time": "2008-01-01",
    "end_time": "2020-08-01",
    "fit_start_time": "2008-01-01",
    "fit_end_time": "2014-12-31",
    # "start_time": "2020-01-01",
    # "end_time": "2020-02-21",
    # "fit_start_time": "2020-01-01",  # 模型跑数据的开始时间
    # "fit_end_time": "2020-01-31",
    "instruments": market,
    "infer_processors" : [
                                    {'class': 'FilterCol',
                                     'kwargs': {'fields_group': 'feature', 
                                                'col_list': ["RESI5", "WVMA5", "RSQR5", "KLEN", "RSQR10", "CORR5", "CORD5", "CORR10", 
                            "ROC60", "RESI10", "VSTD5", "RSQR60", "CORR60", "WVMA60", "STD5", 
                            "RSQR20", "CORD60", "CORD10", "CORR20", "KLOW"
                        ]
                                     }},
                                    {'class': 'RobustZScoreNorm', # RobustZScoreNorm和Fillna，用于进行标准化和填充缺失值。
                                     'kwargs': {'fields_group': 'feature', 
                                                'clip_outlier': True}},
                                    {'class': 'Fillna', 
                                     'kwargs': {'fields_group': 'feature'}}],
    "learn_processors": [{'class': 'DropnaLabel'}, #DropnaLabel删除标注中含有缺失值的样本。

                                    # 对预测的目标进行截面排序处理  DropnaLabel 和 CSRankNorm 预处理器，用于对标签进行处理。
                                    {'class': 'CSRankNorm', 'kwargs': {'fields_group': 'label'}}],

                                    # 预测的目标
                                    'label': ["Ref($close, -2) / Ref($close, -1) - 1"] ,#下一日收益率, Ref($close, -1)表示下一日收盘价
                                    
}
    
# 任务参数配置
task = {
    "model": {  # 模型参数配置
        # 模型类
        "class": "TransformerModel",
        # 模型类所在模块
        "module_path": "qlib.contrib.model.pytorch_transformer_ts_cw_nhead",
        "kwargs": {  # 模型超参数配置
            'seed': 0,
            'n_jobs': 20,
            'GPU':1,
        }, 
    },
    "dataset": {  # 　因子库数据集参数配置
        # 数据集类，是Dataset with Data(H)andler的缩写，即带数据处理器的数据集
        "class": "TSDatasetH",
        # 数据集类所在模块
        "module_path": "qlib.data.dataset",
        "kwargs": {  # 数据集参数配置
            "handler": {  # 数据集使用的数据处理器配置
                #"class": "Alpha158",  # 数据处理器类，继承自DataHandlerLP
                "module_path": "qlib.contrib.data.handler",  # 数据处理器类所在模块
                "class": "Alpha158",
                "kwargs": data_handler_config,  # 数据处理器参数配置
            },
            "segments": {  # 数据集划分标准
                "train": ("2008-01-01", "2014-12-31"), # 此时段的数据为训练集
                "valid": ("2015-01-01", "2016-12-31"), # 此时段的数据为验证集
                "test": ("2017-01-01", "2020-08-01"),  # 此时段的数据为测试集
                # "train": ("2020-01-01", "2020-01-31"),  # 此时段的数据为训练集
                # "valid": ("2020-01-31", "2020-02-20"),  # 此时段的数据为验证集
                # "test": ("2020-02-20", "2020-02-21"),  # 此时段的数据为测试集
            },
        },
    },

}

# 实例化模型对象
model = init_instance_by_config(task["model"])

# 实例化因子库数据集，从基础行情数据计算出的包含所有特征（因子）和标签值的数据集。
dataset = init_instance_by_config(task["dataset"])  # DatasetH

ModuleNotFoundError. CatBoostModel are skipped. (optional: maybe installing CatBoostModel can fix it.)
ModuleNotFoundError. XGBModel is skipped(optional: maybe installing xgboost can fix it).


/home/shared/anaconda3/envs/seg/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[38281:MainThread](2023-07-08 14:56:19,735) INFO - qlib.Initialization - [config.py:413] - default_conf: client.
[38281:MainThread](2023-07-08 14:56:19,740) INFO - qlib.workflow - [expm.py:31] - experiment manager uri is at file:/home/shared/qlib-main/mlruns
[38281:MainThread](2023-07-08 14:56:19,741) INFO - qlib.Initialization - [__init__.py:74] - qlib successfully initialized based on client settings.
[38281:MainThread](2023-07-08 14:56:19,743) INFO - qlib.Initialization - [__init__.py:76] - data_path={'__DEFAULT_FREQ': PosixPath('/home/shared/qlib-main/qlib_data/cn_data')}
[38281:MainThread](2023-07-08 14:56:20,003) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:77] - Naive Transformer:
batch_size : 409

In [2]:
# start exp to train model
with R.start(experiment_name="train_model"):
    R.log_params(**flatten_dict(task))
    model.fit(dataset)
    R.save_objects(trained_model=model)
    rid = R.get_recorder().id

[38281:MainThread](2023-07-08 14:57:21,640) INFO - qlib.workflow - [expm.py:316] - <mlflow.tracking.client.MlflowClient object at 0x7fa84c144bb0>
[38281:MainThread](2023-07-08 14:57:21,651) INFO - qlib.workflow - [exp.py:260] - Experiment 1 starts running ...
[38281:MainThread](2023-07-08 14:57:21,999) INFO - qlib.workflow - [recorder.py:339] - Recorder 7b920ab9ebe2447cbcab41a04f72562f starts running under Experiment 1 ...
Not a git repository
To compare two paths outside a working tree:
usage: git diff [--no-index] <path> <path>
[38281:MainThread](2023-07-08 14:57:22,095) INFO - qlib.workflow - [recorder.py:372] - Fail to log the uncommitted code of $CWD when run `git diff`
fatal: 不是一个 git 仓库（或者直至挂载点 / 的任何父目录）
停止在文件系统边界（未设置 GIT_DISCOVERY_ACROSS_FILESYSTEM）。
[38281:MainThread](2023-07-08 14:57:22,205) INFO - qlib.workflow - [recorder.py:372] - Fail to log the uncommitted code of $CWD when run `git status`
Not a git repository
To compare two paths outside a working tree:
usage: git diff

[38281:MainThread](2023-07-09 04:51:54,556) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:292] - evaluating...
[38281:MainThread](2023-07-09 04:52:42,644) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:295] - train -0.998137, valid -0.999850
[38281:MainThread](2023-07-09 04:52:42,654) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:289] - Epoch2:
[38281:MainThread](2023-07-09 04:52:42,655) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:290] - training...


[38281:MainThread](2023-07-09 11:42:47,844) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:292] - evaluating...
[38281:MainThread](2023-07-09 11:43:29,406) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:295] - train -0.991724, valid -0.994822
[38281:MainThread](2023-07-09 11:43:29,424) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:289] - Epoch3:
[38281:MainThread](2023-07-09 11:43:29,426) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:290] - training...


[38281:MainThread](2023-07-09 17:27:18,025) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:292] - evaluating...
[38281:MainThread](2023-07-09 17:28:00,194) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:295] - train -0.991877, valid -0.995890
[38281:MainThread](2023-07-09 17:28:00,198) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:289] - Epoch4:
[38281:MainThread](2023-07-09 17:28:00,199) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:290] - training...


[38281:MainThread](2023-07-10 01:16:35,526) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:292] - evaluating...
[38281:MainThread](2023-07-10 01:17:53,781) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:295] - train -0.997657, valid -1.001560
[38281:MainThread](2023-07-10 01:17:53,799) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:289] - Epoch5:
[38281:MainThread](2023-07-10 01:17:53,803) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:290] - training...


[38281:MainThread](2023-07-10 15:32:37,653) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:292] - evaluating...
[38281:MainThread](2023-07-10 15:33:59,663) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:295] - train -0.991447, valid -0.996595
[38281:MainThread](2023-07-10 15:33:59,667) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:307] - early stop
[38281:MainThread](2023-07-10 15:33:59,672) INFO - qlib.TransformerModel - [pytorch_transformer_ts_cw_nhead.py:315] - best score: -0.994822 @ 2
[38281:MainThread](2023-07-10 15:34:00,611) INFO - qlib.timer - [log.py:117] - Time cost: 0.000s | waiting `async_log` Done


In [3]:
###################################
# prediction, backtest & analysis
###################################
port_analysis_config = {
    "executor": {
        "class": "SimulatorExecutor",
        "module_path": "qlib.backtest.executor",
        "kwargs": {
            "time_per_step": "day",
            "generate_portfolio_metrics": True,
        },
    },
    "strategy": {
        "class": "TopkDropoutStrategy",
        "module_path": "qlib.contrib.strategy",
        "kwargs": {
            "model": model,
            "dataset": dataset,
            "topk": 50,
            "n_drop": 5,
        },
    },
    "backtest": {
        "start_time": "2017-01-01",
        "end_time": "2020-08-01",
        "account": 100000000,
        "benchmark": benchmark,
        "exchange_kwargs": {
            "freq": "day",
            "limit_threshold": 0.095,
            "deal_price": "close",
            "open_cost": 0.0005,
            "close_cost": 0.0015,
            "min_cost": 5,
        },
    },
}

# backtest and analysis
with R.start(experiment_name="backtest_analysis"):
    recorder = R.get_recorder(recorder_id=rid, experiment_name="train_model")
    model = recorder.load_object("trained_model")

    # prediction
    recorder = R.get_recorder()
    ba_rid = recorder.id
    sr = SignalRecord(model, dataset, recorder)
    sr.generate()

    # backtest & analysis
    par = PortAnaRecord(recorder, port_analysis_config, "day")
    par.generate()

[38281:MainThread](2023-07-10 15:34:24,200) INFO - qlib.workflow - [expm.py:316] - <mlflow.tracking.client.MlflowClient object at 0x7fa835928550>
[38281:MainThread](2023-07-10 15:34:24,218) INFO - qlib.workflow - [exp.py:260] - Experiment 2 starts running ...
[38281:MainThread](2023-07-10 15:34:24,305) INFO - qlib.workflow - [recorder.py:339] - Recorder 306deaaa04cd438b894d4c2239ca5826 starts running under Experiment 2 ...
Not a git repository
To compare two paths outside a working tree:
usage: git diff [--no-index] <path> <path>
[38281:MainThread](2023-07-10 15:34:24,599) INFO - qlib.workflow - [recorder.py:372] - Fail to log the uncommitted code of $CWD when run `git diff`
fatal: 不是一个 git 仓库（或者直至挂载点 / 的任何父目录）
停止在文件系统边界（未设置 GIT_DISCOVERY_ACROSS_FILESYSTEM）。
[38281:MainThread](2023-07-10 15:34:24,877) INFO - qlib.workflow - [recorder.py:372] - Fail to log the uncommitted code of $CWD when run `git status`
Not a git repository
To compare two paths outside a working tree:
usage: git diff

'The following are prediction results of the TransformerModel model.'
                          score
datetime   instrument          
2017-01-03 SH600000   -0.019650
           SH600008    0.044811
           SH600009    0.097904
           SH600010    0.058627
           SH600015    0.023815


[38281:MainThread](2023-07-10 15:34:48,347) INFO - qlib.backtest caller - [__init__.py:94] - Create new exchange
[38281:MainThread](2023-07-10 15:35:06,314) WARNING - qlib.online operator - [exchange.py:216] - factor.day.bin file not exists or factor contains `nan`. Order using adjusted_price.
[38281:MainThread](2023-07-10 15:35:06,319) WARNING - qlib.online operator - [exchange.py:218] - trade unit 100 is not supported in adjusted_price mode.
[38281:MainThread](2023-07-10 15:35:27,306) WARNING - qlib.data - [data.py:662] - load calendar error: freq=day, future=True; return current calendar!
[38281:MainThread](2023-07-10 15:35:27,309) WARNING - qlib.data - [data.py:665] - You can get future calendar by referring to the following document: https://github.com/microsoft/qlib/blob/main/scripts/data_collector/contrib/README.md
[38281:MainThread](2023-07-10 15:35:27,337) WARNING - qlib.BaseExecutor - [executor.py:121] - `common_infra` is not set for <qlib.backtest.executor.SimulatorExecutor 

'The following are analysis results of benchmark return(1day).'
                       risk
mean               0.000477
std                0.012295
annualized_return  0.113561
information_ratio  0.598699
max_drawdown      -0.370479
'The following are analysis results of the excess return without cost(1day).'
                       risk
mean               0.000321
std                0.004988
annualized_return  0.076312
information_ratio  0.991700
max_drawdown      -0.105341
'The following are analysis results of the excess return with cost(1day).'
                       risk
mean               0.000141
std                0.004987
annualized_return  0.033454
information_ratio  0.434852
max_drawdown      -0.122887
'The following are analysis results of indicators(1day).'
     value
ffr    1.0
pa     0.0
pos    0.0


In [4]:

# 从实验记录器加载保存在pkl文件中的预测结果数据
pred_df = recorder.load_object("pred.pkl")

# 从实验记录器加载保存在pkl文件中的标签数据
label_df = recorder.load_object("label.pkl")
label_df.columns = ['label']

# 构造预测值和标签值并列的df
pred_label = pd.concat([pred_df, label_df], axis=1, sort=True).reindex(label_df.index)

print(pred_label)

                          score     label
datetime   instrument                    
2017-01-03 SH600000   -0.019650 -0.001831
           SH600008    0.044811 -0.002398
           SH600009    0.097904  0.001493
           SH600010    0.058627  0.003520
           SH600015    0.023815 -0.007142
...                         ...       ...
2020-07-31 SZ300413   -0.082126 -0.037566
           SZ300433   -0.002028 -0.031677
           SZ300498   -0.047887 -0.006531
           SZ300601   -0.086896  0.090264
           SZ300628    0.018619  0.004142

[261300 rows x 2 columns]


In [5]:
from qlib.contrib.eva.alpha import calc_ic, calc_long_short_return

ic, ric = calc_ic(pred_df.iloc[:, 0], label_df.iloc[:, 0])
long_short_r, long_avg_r = calc_long_short_return(pred_df.iloc[:, 0], label_df.iloc[:, 0])
ic = ic.mean()
ric = ric.mean()
print("ic的平均值为:" ,ic)
print("ric的平均值为:", ric)

ic的平均值为: 0.02482547370544914
ric的平均值为: 0.03754627505367014


In [6]:
from qlib.contrib.report import analysis_model, analysis_position
from qlib.data import D
recorder = R.get_recorder(recorder_id=ba_rid, experiment_name="backtest_analysis")
print(recorder)
pred_df = recorder.load_object("pred.pkl")
pred_df_dates = pred_df.index.get_level_values(level='datetime') #提取pred_df中的日期信息，将日期数据提取到pred_df_dates变量中。
report_normal_df = recorder.load_object("portfolio_analysis/report_normal_1day.pkl")#加载了保存的标准报告（portfolio report）数据，将其赋值给report_normal_df变量。
positions = recorder.load_object("portfolio_analysis/positions_normal_1day.pkl")#加载了保存的仓位数据，将其赋值给positions变量。
analysis_df = recorder.load_object("portfolio_analysis/port_analysis_1day.pkl")#加载了保存的组合分析数据，将其赋值给analysis_df变量。

{'class': 'Recorder', 'id': '306deaaa04cd438b894d4c2239ca5826', 'name': 'mlflow_recorder', 'experiment_id': '2', 'start_time': '2023-07-10 15:34:24', 'end_time': '2023-07-10 15:36:16', 'status': 'FINISHED'}


In [7]:
## 总体报告 传入参数report_normal_df，生成总体报告的图形。如果show_notebook参数设置为True，则图形将在笔记本中显示。如果设置为False，则图形将在独立的窗口中显示。
report_graph = analysis_position.report_graph(report_normal_df, show_notebook=False)
for fig in report_graph: #report_graph是一个包含多个图形对象的列表，每个图形对象代表总体报告中的一个图形。
    fig.show()


In [8]:
## 最大回撤
risk_analysis_graph = analysis_position.risk_analysis_graph(analysis_df, report_normal_df, show_notebook=False)
for fig in risk_analysis_graph:
    fig.show()

In [9]:
## 累计回报
model_performance_graph = analysis_model.model_performance_graph(pred_label, show_notebook=False)
for fig in model_performance_graph:
    fig.show()


In [10]:
# 绘制信息系数图 ic、 rank ic
analysis_position.score_ic_graph(pred_label)

In [11]:
analysis_df

risk
excess_return_without_cost mean               0.000321
                           std                0.004988
                           annualized_return  0.076312
                           information_ratio  0.991700
                           max_drawdown      -0.105341
excess_return_with_cost    mean               0.000141
                           std                0.004987
                           annualized_return  0.033454
                           information_ratio  0.434852
                           max_drawdown      -0.122887